## A workbook companion to the introduction to the DataFrames.jl package

*version: 2023-02-12* for DataFrames v1.5.0 and Julia v1.9.0

[Bogumił Kamiński](http://bogumilkaminski.pl/about/)

## Getting ready

We will use [this](http://archive.ics.uci.edu/ml/datasets/communities+and+crime) dataset. So first we download the required files.

In [1]:
using DataFrames
using CSV
using FreqTables
using Plots, StatsPlots
using GLM
using Statistics

## Loading the data

Here we have to do some non-standard operations.

In [2]:
colnamelines = filter(line -> startswith(line, "@attribute"), readlines("meta.txt"))

128-element Vector{String}:
 "@attribute state numeric"
 "@attribute county numeric"
 "@attribute community numeric"
 "@attribute communityname string"
 "@attribute fold numeric"
 "@attribute population numeric"
 "@attribute householdsize numeric"
 "@attribute racepctblack numeric"
 "@attribute racePctWhite numeric"
 "@attribute racePctAsian numeric"
 "@attribute racePctHisp numeric"
 "@attribute agePct12t21 numeric"
 "@attribute agePct12t29 numeric"
 ⋮
 "@attribute NumKindsDrugsSeiz numeric"
 "@attribute PolicAveOTWorked numeric"
 "@attribute LandArea numeric"
 "@attribute PopDens numeric"
 "@attribute PctUsePubTrans numeric"
 "@attribute PolicCars numeric"
 "@attribute PolicOperBudg numeric"
 "@attribute LemasPctPolicOnPatr numeric"
 "@attribute LemasGangUnitDeploy numeric"
 "@attribute LemasPctOfficDrugUn numeric"
 "@attribute PolicBudgPerPop numeric"
 "@attribute ViolentCrimesPerPop numeric"

We need to convert column names to `Symbol` as this is the type that CSV.jl expects.

In [3]:
colnames = Symbol.(getindex.(split.(colnamelines), 2))

128-element Vector{Symbol}:
 :state
 :county
 :community
 :communityname
 :fold
 :population
 :householdsize
 :racepctblack
 :racePctWhite
 :racePctAsian
 :racePctHisp
 :agePct12t21
 :agePct12t29
 ⋮
 :NumKindsDrugsSeiz
 :PolicAveOTWorked
 :LandArea
 :PopDens
 :PctUsePubTrans
 :PolicCars
 :PolicOperBudg
 :LemasPctPolicOnPatr
 :LemasGangUnitDeploy
 :LemasPctOfficDrugUn
 :PolicBudgPerPop
 :ViolentCrimesPerPop

In [4]:
coltypes = getindex.(split.(colnamelines), 3)

128-element Vector{SubString{String}}:
 "numeric"
 "numeric"
 "numeric"
 "string"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 ⋮
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"
 "numeric"

In [5]:
df = CSV.read("data.txt", DataFrame, header=colnames)

1994×128 DataFrame
  Row │ state  county   community  communityname           fold   population   ⋯
      │ Int64  String3  String7    String31                Int64  Float64      ⋯
──────┼─────────────────────────────────────────────────────────────────────────
    1 │     8  ?        ?          Lakewoodcity                1        0.19   ⋯
    2 │    53  ?        ?          Tukwilacity                 1        0.0
    3 │    24  ?        ?          Aberdeentown                1        0.0
    4 │    34  5        81440      Willingborotownship         1        0.04
    5 │    42  95       6096       Bethlehemtownship           1        0.01   ⋯
    6 │     6  ?        ?          SouthPasadenacity           1        0.02
    7 │    44  7        41500      Lincolntown                 1        0.01
    8 │     6  ?        ?          Selmacity                   1        0.01
    9 │    21  ?        ?          Hendersoncity               1        0.03   ⋯
   10 │    29  ?        ?          Claytoncity                 1        0.01
   11 │     6  ?        ?          DalyCitycity                1        0.13
  ⋮   │   ⋮       ⋮         ⋮                ⋮               ⋮        ⋮        ⋱
 1985 │    39  95       48342      Maumeecity                 10        0.01
 1986 │     1  ?        ?          AlexanderCitycity          10        0.01   ⋯
 1987 │     9  3        70550      Southingtontown            10        0.05
 1988 │    44  7        11800      Burrillvilletown           10        0.01
 1989 │    28  ?        ?          Columbuscity               10        0.02
 1990 │    12  ?        ?          TempleTerracecity          10        0.01   ⋯
 1991 │     6  ?        ?          Seasidecity                10        0.05
 1992 │     9  9        80070      Waterburytown              10        0.16
 1993 │    25  17       72600      Walthamcity                10        0.08
 1994 │     6  ?        ?          Ontariocity                10        0.2    ⋯
                                               122 columns and 1973 rows omitted

We see that theere is a problem that `?` indicates a missing value in the data set

In [6]:
df = CSV.read("data.txt", DataFrame, header=colnames, missingstring="?")

1994×128 DataFrame
  Row │ state  county   community  communityname           fold   population   ⋯
      │ Int64  Int64?   Int64?     String31                Int64  Float64      ⋯
──────┼─────────────────────────────────────────────────────────────────────────
    1 │     8  missing    missing  Lakewoodcity                1        0.19   ⋯
    2 │    53  missing    missing  Tukwilacity                 1        0.0
    3 │    24  missing    missing  Aberdeentown                1        0.0
    4 │    34        5      81440  Willingborotownship         1        0.04
    5 │    42       95       6096  Bethlehemtownship           1        0.01   ⋯
    6 │     6  missing    missing  SouthPasadenacity           1        0.02
    7 │    44        7      41500  Lincolntown                 1        0.01
    8 │     6  missing    missing  Selmacity                   1        0.01
    9 │    21  missing    missing  Hendersoncity               1        0.03   ⋯
   10 │    29  missing    missing  Claytoncity                 1        0.01
   11 │     6  missing    missing  DalyCitycity                1        0.13
  ⋮   │   ⋮       ⋮         ⋮                ⋮               ⋮        ⋮        ⋱
 1985 │    39       95      48342  Maumeecity                 10        0.01
 1986 │     1  missing    missing  AlexanderCitycity          10        0.01   ⋯
 1987 │     9        3      70550  Southingtontown            10        0.05
 1988 │    44        7      11800  Burrillvilletown           10        0.01
 1989 │    28  missing    missing  Columbuscity               10        0.02
 1990 │    12  missing    missing  TempleTerracecity          10        0.01   ⋯
 1991 │     6  missing    missing  Seasidecity                10        0.05
 1992 │     9        9      80070  Waterburytown              10        0.16
 1993 │    25       17      72600  Walthamcity                10        0.08
 1994 │     6  missing    missing  Ontariocity                10        0.2    ⋯
                                               122 columns and 1973 rows omitted

Let us check if what we detected is consistent with the metadata

In [7]:
freqtable(eltype.(eachcol(df)), coltypes)

5×2 Named Matrix{Int64}
            Dim1 ╲ Dim2 │ "numeric"   "string"
────────────────────────┼─────────────────────
Union{Missing, Int64}   │         2          0
Int64                   │         2          0
Union{Missing, Float64} │        23          0
String31                │         0          1
Float64                 │       100          0

In [8]:
describe(df)

128×7 DataFrame
 Row │ variable             mean       min           median   max              ⋯
     │ Symbol               Union…     Any           Union…   Any              ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ state                28.6836    1             34.0     56               ⋯
   2 │ county               58.8268    1             23.0     840
   3 │ community            46188.3    70            48090.0  94597
   4 │ communityname                   Aberdeencity           Zanesvillecity
   5 │ fold                 5.49398    1             5.0      10               ⋯
   6 │ population           0.0575928  0.0           0.02     1.0
   7 │ householdsize        0.463395   0.0           0.44     1.0
   8 │ racepctblack         0.179629   0.0           0.06     1.0
   9 │ racePctWhite         0.753716   0.0           0.85     1.0              ⋯
  10 │ racePctAsian         0.153681   0.0           0.07     1.0
  11 │ racePctHisp          0.144022   0.0           0.04     1.0
  ⋮  │          ⋮               ⋮           ⋮           ⋮           ⋮          ⋱
 119 │ LandArea             0.0652307  0.0           0.04     1.0
 120 │ PopDens              0.232854   0.0           0.17     1.0              ⋯
 121 │ PctUsePubTrans       0.161685   0.0           0.07     1.0
 122 │ PolicCars            0.163103   0.0           0.08     1.0
 123 │ PolicOperBudg        0.0767085  0.0           0.03     1.0
 124 │ LemasPctPolicOnPatr  0.698589   0.0           0.75     1.0              ⋯
 125 │ LemasGangUnitDeploy  0.440439   0.0           0.5      1.0
 126 │ LemasPctOfficDrugUn  0.0940522  0.0           0.0      1.0
 127 │ PolicBudgPerPop      0.195078   0.0           0.15     1.0
 128 │ ViolentCrimesPerPop  0.237979   0.0           0.15     1.0              ⋯
                                                  2 columns and 107 rows omitted

## Analyzing the data

We will not want to use the first five columns from the data set. Let us get rid of them. This will be an in-place operation.

In [9]:
select!(df, Not(1:5))

1994×123 DataFrame
  Row │ population  householdsize  racepctblack  racePctWhite  racePctAsian  r ⋯
      │ Float64     Float64        Float64       Float64       Float64       F ⋯
──────┼─────────────────────────────────────────────────────────────────────────
    1 │       0.19           0.33          0.02          0.9           0.12    ⋯
    2 │       0.0            0.16          0.12          0.74          0.45
    3 │       0.0            0.42          0.49          0.56          0.17
    4 │       0.04           0.77          1.0           0.08          0.12
    5 │       0.01           0.55          0.02          0.95          0.09    ⋯
    6 │       0.02           0.28          0.06          0.54          1.0
    7 │       0.01           0.39          0.0           0.98          0.06
    8 │       0.01           0.74          0.03          0.46          0.2
    9 │       0.03           0.34          0.2           0.84          0.02    ⋯
   10 │       0.01           0.4           0.06          0.87          0.3
   11 │       0.13           0.71          0.15          0.07          1.0
  ⋮   │     ⋮             ⋮             ⋮             ⋮             ⋮          ⋱
 1985 │       0.01           0.43          0.01          0.98          0.03
 1986 │       0.01           0.41          0.55          0.57          0.01    ⋯
 1987 │       0.05           0.52          0.02          0.97          0.04
 1988 │       0.01           0.65          0.0           1.0           0.01
 1989 │       0.02           0.41          1.0           0.21          0.02
 1990 │       0.01           0.4           0.1           0.87          0.12    ⋯
 1991 │       0.05           0.96          0.46          0.28          0.83
 1992 │       0.16           0.37          0.25          0.69          0.04
 1993 │       0.08           0.51          0.06          0.87          0.22
 1994 │       0.2            0.78          0.14          0.46          0.24    ⋯
                                               118 columns and 1973 rows omitted

Analyzing the correlation between `:ViolentCrimesPerProp` and other variables.

The challenge is that some of the variables have missing data and other do not have them. We want to use pairwise complete observations approach (delete only what we have to delete when calculating the correlation).

This will be our fisrst encounter with views of a `DataFrame`. The use of `@view` avoids copying of the data. This improves the performance, but in general you should not mutate the view, as the changes will propagate back to the parent.

In [10]:
results = DataFrame()
for col in names(df, Not("ViolentCrimesPerPop"))
    cols = [col, "ViolentCrimesPerPop"]
    subdf = @view df[completecases(df, cols), cols]
    push!(results, (vairable=col, correlation=cor(subdf[!, 1], subdf[!, 2])))
end

In [11]:
results

122×2 DataFrame
 Row │ vairable             correlation 
     │ String               Float64     
─────┼──────────────────────────────────
   1 │ population             0.367157
   2 │ householdsize         -0.0349226
   3 │ racepctblack           0.631264
   4 │ racePctWhite          -0.68477
   5 │ racePctAsian           0.0376218
   6 │ racePctHisp            0.29305
   7 │ agePct12t21            0.0604772
   8 │ agePct12t29            0.153357
   9 │ agePct16t24            0.0993467
  10 │ agePct65up             0.0671715
  11 │ numbUrban              0.362897
  ⋮  │          ⋮                ⋮
 113 │ PolicAveOTWorked       0.0336298
 114 │ LandArea               0.1968
 115 │ PopDens                0.28139
 116 │ PctUsePubTrans         0.153829
 117 │ PolicCars              0.381742
 118 │ PolicOperBudg          0.33819
 119 │ LemasPctPolicOnPatr   -0.082317
 120 │ LemasGangUnitDeploy    0.116163
 121 │ LemasPctOfficDrugUn    0.348627
 122 │ PolicBudgPerPop        0.0959612
                        101 rows omitted

What if we want to see the most correlated values on top of the data frame?

In [12]:
sort!(results, :correlation, by = abs, rev=true)

122×2 DataFrame
 Row │ vairable               correlation 
     │ String                 Float64     
─────┼────────────────────────────────────
   1 │ PctKids2Par             -0.738424
   2 │ PctIlleg                 0.737957
   3 │ PctFam2Par              -0.706667
   4 │ racePctWhite            -0.68477
   5 │ PctYoungKids2Par        -0.666059
   6 │ PctTeen2Par             -0.661582
   7 │ racepctblack             0.631264
   8 │ pctWInvInc              -0.576324
   9 │ pctWPubAsst              0.574665
  10 │ FemalePctDiv             0.556032
  11 │ TotalPctDiv              0.552777
  ⋮  │           ⋮                 ⋮
 113 │ agePct12t21              0.0604772
 114 │ MedOwnCostPctIncNoMtg    0.0537633
 115 │ PctEmplManu             -0.044906
 116 │ PersPerOccupHous        -0.0397391
 117 │ racePctAsian             0.0376218
 118 │ householdsize           -0.0349226
 119 │ PolicAveOTWorked         0.0336298
 120 │ PctWorkMomYoungKids     -0.0225354
 121 │ PctVacMore6Mos           0.0212828
 122 │ PctSameState85          -0.0194589
                          101 rows omitted

Now let us do some additional analyses.

In [13]:
@df select(df, [results[1:4, 1]; "ViolentCrimesPerPop"]) corrplot(cols(1:5))

In [14]:
lm(@formula(ViolentCrimesPerPop ~ PctKids2Par + PctIlleg + racePctWhite), df)

StatsModels.TableRegressionModel{LinearModel{GLM.LmResp{Vector{Float64}}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}, Vector{Int64}}}}, Matrix{Float64}}

ViolentCrimesPerPop ~ 1 + PctKids2Par + PctIlleg + racePctWhite

Coefficients:
───────────────────────────────────────────────────────────────────────────
                  Coef.  Std. Error       t  Pr(>|t|)  Lower 95%  Upper 95%
───────────────────────────────────────────────────────────────────────────
(Intercept)    0.649797   0.0343578   18.91    <1e-72   0.582416   0.717178
PctKids2Par   -0.444269   0.0322473  -13.78    <1e-40  -0.507511  -0.381027
PctIlleg       0.192406   0.0346147    5.56    <1e-07   0.124521   0.260291
racePctWhite  -0.244363   0.0225653  -10.83    <1e-25  -0.288617  -0.200108
───────────────────────────────────────────────────────────────────────────

Now feel free to experiment with the data set.